In [ ]:
!pip install transformers
!pip install datasets
!pip install evaluate
!pip install jiwer
!pip install accelerate

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 527.3/527.3 kB 22.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 116.3/116.3 kB 6.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 39.9/39.9 MB 17.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 134.8/134.8 kB 10.9 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 194.1/194.1 kB 15.1 MB/s eta 0:00:00
  Attempting uninstall: pyarrow
    Found existing installation: pyarrow 14.0.2
    Uninstalling pyarrow-14.0.2:
      Successfully uninstalled pyarrow-14.0.2
ERROR: pip's dependency resolver does not currently take into account all the packages that are installed. This behaviour is the source of the following dependency conflicts.
cudf-cu12 24.4.1 requires pyarrow<15.0.0a0,>=14.0.1, but you have pyarrow 17.0.0 which is incompatible.
ibis-framework 8.0.0 requires pyarrow<16,>=2, but you have pyarrow 17.0.0 which is incompatible.
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 84.1/84.1 kB 162.5 

In [ ]:
from datasets import load_dataset, Audio
from transformers import AutoProcessor, AutoModelForCTC, TrainingArguments, Trainer, pipeline
import torch
from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union
import evaluate
import numpy as np


In [ ]:
from datasets import load_dataset, Audio
# load the dataset.
# you may get "can't be fetched" error if the server of the dataset is down
minds = load_dataset("PolyAI/minds14", name="en-US", split="train[:400]")
# split the data into training and testing sets
minds = minds.train_test_split(test_size=0.2)
# removing useless columns
minds = minds.remove_columns(
	["english_transcription", "intent_class", "lang_id"])
# preparing all the audio files in a fixed sampling rate of 16000
minds = minds.cast_column("audio", Audio(sampling_rate=16_000))


/usr/local/lib/python3.10/dist-packages/huggingface_hub/utils/_token.py:89: UserWarning: 
The secret `HF_TOKEN` does not exist in your Colab secrets.
To authenticate with the Hugging Face Hub, create a token in your settings tab (https://huggingface.co/settings/tokens), set it as secret in your Google Colab and restart your session.
You will be able to reuse this secret in all of your notebooks.
Please note that authentication is recommended but still optional to access public models or datasets.
  warnings.warn(


The repository for PolyAI/minds14 contains custom code which must be executed to correctly load the dataset. You can inspect the repository content at https://hf.co/datasets/PolyAI/minds14.
You can avoid this prompt in future by passing the argument `trust_remote_code=True`.

Do you wish to run the custom code? [y/N] y


Generating train split: 0 examples [00:00, ? examples/s]

In [ ]:
from transformers import AutoProcessor

processor = AutoProcessor.from_pretrained("facebook/wav2vec2-base")


preprocessor_config.json:   0%|          | 0.00/159 [00:00<?, ?B/s]

tokenizer_config.json:   0%|          | 0.00/163 [00:00<?, ?B/s]

config.json:   0%|          | 0.00/1.84k [00:00<?, ?B/s]

/usr/local/lib/python3.10/dist-packages/transformers/configuration_utils.py:364: UserWarning: Passing `gradient_checkpointing` to a config initialization is deprecated and will be removed in v5 Transformers. Using `model.gradient_checkpointing_enable()` instead, or if you are using the `Trainer` API, pass `gradient_checkpointing=True` in your `TrainingArguments`.
  warnings.warn(


vocab.json:   0%|          | 0.00/291 [00:00<?, ?B/s]

special_tokens_map.json:   0%|          | 0.00/85.0 [00:00<?, ?B/s]

In [ ]:
def uppercase(example):
	return {"transcription": example["transcription"].upper()}


minds = minds.map(uppercase)


def prepare_dataset(batch):
	audio = batch["audio"]
	batch = processor(audio["array"],
					sampling_rate=audio["sampling_rate"],
					text=batch["transcription"])
	batch["input_length"] = len(batch["input_values"][0])
	return batch


encoded_minds = minds.map(
	prepare_dataset, remove_columns=minds.column_names["train"], num_proc=16)


Map:   0%|          | 0/320 [00:00<?, ? examples/s]

Map:   0%|          | 0/80 [00:00<?, ? examples/s]

/usr/local/lib/python3.10/dist-packages/multiprocess/popen_fork.py:66: RuntimeWarning: os.fork() was called. os.fork() is incompatible with multithreaded code, and JAX is multithreaded, so this will likely lead to a deadlock.
  self.pid = os.fork()


Map (num_proc=16):   0%|          | 0/320 [00:00<?, ? examples/s]

Map (num_proc=16):   0%|          | 0/80 [00:00<?, ? examples/s]

In [ ]:
import torch
from dataclasses import dataclass, field
from typing import Any, Dict, List, Optional, Union

@dataclass
class DataCollatorCTCWithPadding:
	processor: AutoProcessor
	padding: Union[bool, str] = "longest"

	def __call__(self, features: List[Dict[str, Union[List[int], torch.Tensor]]]) -> Dict[str, torch.Tensor]:
		# split inputs and labels since they have to be of different lengths and need different padding methods
		input_features = [{"input_values": feature["input_values"][0]} for feature in features]
		label_features = [{"input_ids": feature["labels"]} for feature in features]

		batch = self.processor.pad(input_features, padding=self.padding, return_tensors="pt")

		labels_batch = self.processor.pad(labels=label_features, padding=self.padding, return_tensors="pt")

		# To reduce lose more efficiently we will replace the padding with (-100)
		labels = labels_batch["input_ids"].masked_fill(labels_batch.attention_mask.ne(1), -100)

		batch["labels"] = labels

		return batch

data_collator = DataCollatorCTCWithPadding(processor=processor, padding="longest")


In [ ]:
wer = evaluate.load("wer")

def compute_metrics(pred):
	pred_logits = pred.predictions
	pred_ids = np.argmax(pred_logits, axis=-1)

	pred.label_ids[pred.label_ids == -100] = processor.tokenizer.pad_token_id

	pred_str = processor.batch_decode(pred_ids)
	label_str = processor.batch_decode(pred.label_ids, group_tokens=False)

	word_error_rate = wer.compute(predictions=pred_str, references=label_str)

	return {"wer": word_error_rate}


In [ ]:
from transformers import AutoModelForCTC, TrainingArguments, Trainer

model = AutoModelForCTC.from_pretrained(
	"facebook/wav2vec2-base",
	ctc_loss_reduction="mean", # better loss reduction but 'avg' can be used
	pad_token_id=processor.tokenizer.pad_token_id,
)


pytorch_model.bin:   0%|          | 0.00/380M [00:00<?, ?B/s]

Some weights of Wav2Vec2ForCTC were not initialized from the model checkpoint at facebook/wav2vec2-base and are newly initialized: ['lm_head.bias', 'lm_head.weight', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original0', 'wav2vec2.encoder.pos_conv_embed.conv.parametrizations.weight.original1']
You should probably TRAIN this model on a down-stream task to be able to use it for predictions and inference.


In [ ]:
training_args = TrainingArguments(
	output_dir="GeeksforGeeks_ASR_CTC_Finetuned",
	per_device_train_batch_size=4,
	gradient_accumulation_steps=2,
	learning_rate=4e-4,	 # increase this if you have good computing resources
	warmup_steps=500, # increase this(if you have sufficient resources) for better transcription(min 500)
	max_steps=1000,	 # increase this(if you have sufficient resources) for better transcription(min 1000)
	gradient_checkpointing=True,
	fp16=True,	 # set this to True if you have GPU enabled to you runtime
	group_by_length=True,
	evaluation_strategy="steps",
	per_device_eval_batch_size=8,
	save_steps=1000,				 # increase this(if you have sufficient resources) for better transcription(min 1000)
	eval_steps=1000,				 # increase this(if you have sufficient resources) for better transcription(min 1000)
	logging_steps=25,
	load_best_model_at_end=True,
	metric_for_best_model="wer",
	greater_is_better=False,
	#push_to_hub=False,
)

trainer = Trainer(
	model=model,
	args=training_args,
	train_dataset=encoded_minds["train"],
	eval_dataset=encoded_minds["test"],
	tokenizer=processor,
	data_collator=data_collator,
	compute_metrics=compute_metrics,
)

trainer.train()


/usr/local/lib/python3.10/dist-packages/transformers/training_args.py:1494: FutureWarning: `evaluation_strategy` is deprecated and will be removed in version 4.46 of 🤗 Transformers. Use `eval_strategy` instead
  warnings.warn(
/usr/local/lib/python3.10/dist-packages/accelerate/accelerator.py:482: FutureWarning: `torch.cuda.amp.GradScaler(args...)` is deprecated. Please use `torch.amp.GradScaler('cuda', args...)` instead.
  self.scaler = torch.cuda.amp.GradScaler(**kwargs)
max_steps is given, it will override any value given in num_train_epochs
/usr/local/lib/python3.10/dist-packages/torch/_dynamo/eval_frame.py:600: UserWarning: torch.utils.checkpoint: the use_reentrant parameter should be passed explicitly. In version 2.4 we will raise an exception if use_reentrant is not passed. use_reentrant=False is recommended, but if you need to preserve the current default behavior, you can pass use_reentrant=True. Refer to docs for more details on the differences between the two variants.
  retu

TrainOutput(global_step=1000, training_loss=5.20044229888916, metrics={'train_runtime': 1490.7539, 'train_samples_per_second': 5.366, 'train_steps_per_second': 0.671, 'total_flos': 1.106271102256128e+18, 'train_loss': 5.20044229888916, 'epoch': 25.0})

In [ ]:
# pipeline for model testing
from transformers import pipeline
dataset = load_dataset("PolyAI/minds14", "en-US", split="train[:25]")
dataset = dataset.cast_column("audio", Audio(sampling_rate=16000))
sampling_rate = dataset.features["audio"].sampling_rate
audio_file = dataset[0]["audio"]["path"]

# load the model check-point
transcriber = pipeline("automatic-speech-recognition",
					model='/content/GeeksforGeeks_ASR_CTC_Finetuned/checkpoint-1000')
transcriber(audio_file)
# actual speech
dataset['transcription'][0]


Hardware accelerator e.g. GPU is available in the environment, but no `device` argument is passed to the `Pipeline` object. Model will be on CPU.


'I would like to set up a joint account with my partner'